In [ ]:
deaths-county-by-county day-by-day
https://raw.githubusercontent.com/CSSEGISandData/COVID-19/master/csse_covid_19_data/csse_covid_19_time_series/time_series_covid19_deaths_US.csv
    
County-by-county daily Sumarry
https://raw.githubusercontent.com/CSSEGISandData/COVID-19/master/csse_covid_19_data/csse_covid_19_daily_reports/05-30-2020.csv   
    
State-by-State Summary   
https://raw.githubusercontent.com/CSSEGISandData/COVID-19/master/csse_covid_19_data/csse_covid_19_daily_reports_us/05-30-2020.csv    

Enter all data from:<br />
https://raw.githubusercontent.com/CSSEGISandData/COVID-19/master/csse_covid_19_data/csse_covid_19_time_series/time_series_covid19_deaths_US.csv  into an Sqlite3 database.<br />    

In [ ]:
!rm data/time_series_covid19_deaths_US.csv.db

In [ ]:
cnt = 0
import time
import sqlite3
import requests as req
import os
DATE = time.strftime("%m-%d-%Y")


# Create an empty list
ALLdata=[]

URL ="https://raw.githubusercontent.com/CSSEGISandData/COVID-19/master/csse_covid_19_data/csse_covid_19_time_series/time_series_covid19_deaths_US.csv"

resp = req.get(URL)
content = resp.text

#clean the content, then break the content into lines 
content=content.replace(",,",",Ex,")
content=content.replace("(","")
content=content.replace(")","")
content=content.replace("\"","")
lines= content.splitlines()
print (len(lines))
# loop the lines one line at a time
# split each line at the delimiter ` , ` 
# then append the empty list 'ALLdata' with the line (which is now a list):  [line] 

# Use the csv filename to name the database
#dbname = "data/"+URL[-33:]+".db"
#print(dbname)

cnt=0
for line in lines:
    cnt=cnt+1
    #convert the splitlines to strings
    if cnt>1:
        line= str(line).split(",")
        ALLdata.append(line)




def create_db(dbname):
    conn = sqlite3.connect(dbname)
    c=conn.cursor()
    c.execute("CREATE TABLE IF NOT EXISTS BINARIES(DATA BLOB,DATE TEXT,COUNTY TEXT,STATE TEXT,LONG FLOAT,LAT FLOAT)")
    conn.commit()
    conn.close()
    return


conn = sqlite3.connect(dbname)
c = conn.cursor()
def insertList(LIST, COUNTY, STATE, LONG, LAT, dbname, c=c):
    DATE = time.strftime("%m-%d-%Y")
    sql = '''INSERT INTO BINARIES
    (DATA, DATE, COUNTY, STATE, LONG, LAT)
    VALUES(?, ?, ?, ?, ?, ?);'''
    c.execute(sql,[sqlite3.Binary(LIST), DATE, COUNTY, STATE, LONG, LAT])
cnt=0
dbname = "data/"+URL[-33:]+".db"
print(dbname)
create_db(dbname)
for i in range(0, len(ALLdata)):
    cnt=cnt+1
    STATE = ALLdata[i][6]
    COUNTY = ALLdata[i][5]
    LONG = float(ALLdata[i][9])
    LAT = float(ALLdata[i][8])
    meta = [ALLdata[i][5],ALLdata[i][6],float(ALLdata[i][8]),float(ALLdata[i][9])]       
    datain = ALLdata[i][14:]
    data = list(map(int, datain))
    BDATA = str(data)
    LIST = str.encode(BDATA)
    insertList(LIST, COUNTY, STATE, LONG, LAT, dbname)        
    if cnt %100==0:
        print(cnt, end= " ")
    if cnt==len(ALLdata): 
        print("\n",cnt)
        conn.commit()
        conn.close()
        
print("\n",cnt)        

## Search the database for data

In [ ]:
import sqlite3
NEW_LIST =[]
def search(County,State,dbname='data/time_series_covid19_deaths_US.csv.db'):
    #dbname = '06-02-2020covid19_deaths.db'
    conn = sqlite3.connect(dbname)
    c = conn.cursor()
    print(County,State)
    cnt=0
    for row in c.execute("SELECT ROWID, * FROM BINARIES"):
        cnt=cnt+1
        # if cnt <10:print(row)
        if County in row and State in row:
            data = row[1].decode()
            print(data,row[2],row[3],row[4],row[5],row[6])
            NEW_LIST.append([data,row[2],row[3],row[4],row[5],row[6]])

print("Example:\n SEARCH: Lorain,Ohio \n")            
SEARCH = input("SEARCH:  ")
SEARCH =SEARCH.split(",")
print("Searching for ... ",SEARCH[0],SEARCH[1])

search(SEARCH[0],SEARCH[1])            

In [ ]:
import time
def get_data(dbname,description):
    conn = sqlite3.connect(dbname)
    c = conn.cursor()
    for row in c.execute('SELECT ROWID, * FROM BINARIES'):
        if description in row[3] or description in row[4]:                 
            data = row[1].decode()
            #data = data.replace("[","").replace("]","")
            DATA = list(eval(data[1:-1]))            
            print(DATA[-2],DATA,row[2],row[3],row[4],row[5],row[6])
    
DATE = time.strftime("%m-%d-%Y")
dbname='data/time_series_covid19_deaths_US.csv.db'
description = "Hillsborough"
get_data(dbname,description)

In [ ]:
!ls data/06-02-2020covid19_deaths.db

In [ ]:
import numpy as np
import struct
from ast import literal_eval
import time
DEATHS = []
NEW_LIST =[]
def search(SEARCH):
    DATE = time.strftime("%m-%d-%Y")
    dbname='data/time_series_covid19_deaths_US.csv.db'
    conn = sqlite3.connect(dbname)
    c = conn.cursor()
    cnt=0
    for row in c.execute("SELECT ROWID, * FROM BINARIES"):
        cnt=cnt+1
        if SEARCH in row[3] or SEARCH in row[4]: 
            data = row[1].decode()
            data = data.replace("[","").replace("]","")
            DATA = list(eval(data))
            num = sum(DATA)
            if num>0 and float(row[6])>0:
                #print(num, end=" ")
                DEATHS.append(DATA)
                print(DATA,row[2],row[3],row[4],row[5],row[6])
                NEW_LIST.append([DATA,row[2],row[3],row[4],row[5],row[6]])
            
#SEARCH = input("SEARCH: ")
SEARCH="Florida"
print(search(SEARCH))

In [ ]:
#print the lists of data from above ` DEATHS.append(data) `
print(DEATHS)

In [ ]:
#Add all the lists together Item by Item

res=[sum(x) for x in zip(*DEATHS)]
print(res) 

In [ ]:
data=[0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 71, 81, 31]

print(data[-1])

In [ ]:
cnt = 0
import time
import sqlite3
import requests as req
import os
DATE = time.strftime("%m-%d-%Y")
import os
dbname = 'data/'+DATE+'covid19deaths.db'
if os.path.exists(dbname):
    os.remove(dbname)
else:
    print("The file does not exist") 


# Create an empty list
ALLdata=[]

URL ="https://raw.githubusercontent.com/CSSEGISandData/COVID-19/master/csse_covid_19_data/csse_covid_19_time_series/time_series_covid19_deaths_US.csv"

resp = req.get(URL)
content = resp.text

#clean the content, then break the content into lines 
content=content.replace(",,",",Ex,")
content=content.replace("(","")
content=content.replace(")","")
content=content.replace("\"","")
lines= content.splitlines()
print (len(lines))
# loop the lines one line at a time
# split each line at the delimiter ` , ` 
# then append the empty list 'ALLdata' with the line (which is now a list):  [line]  
cnt=0
for line in lines:
    cnt=cnt+1
    #convert the splitlines to strings
    if cnt>1:
        line= str(line).split(",")
        ALLdata.append(line)
def create_db(dbname = 'data/'+DATE+'covid19deaths.db'):
    conn = sqlite3.connect(dbname)
    c=conn.cursor()
    c.execute("CREATE TABLE IF NOT EXISTS BINARIES(DATA BLOB,DATE TEXT,COUNTY TEXT,STATE TEXT,LONG FLOAT,LAT FLOAT)")
    conn.commit()
    conn.close()
    return

def insertList(LIST, COUNTY, STATE, LONG, LAT, c=c,dbname = 'data/'+DATE+'covid19deaths.db'):
    conn = sqlite3.connect(dbname)
    c = conn.cursor()
    DATE = time.strftime("%m-%d-%Y")
    sql = '''INSERT INTO BINARIES
    (DATA, DATE, COUNTY, STATE, LONG, LAT)
    VALUES(?, ?, ?, ?, ?, ?);'''
    c.execute(sql,[sqlite3.Binary(LIST), DATE, COUNTY, STATE, LONG, LAT])

    
cnt=0

create_db(dbname = 'data/'+DATE+'covid19deaths.db')
for i in range(0, len(ALLdata)):
    cnt=cnt+1
    STATE = ALLdata[i][6]
    COUNTY = ALLdata[i][5]
    LONG = float(ALLdata[i][9])
    LAT = float(ALLdata[i][8])
    meta = [ALLdata[i][5],ALLdata[i][6],float(ALLdata[i][8]),float(ALLdata[i][9])]       
    datain = ALLdata[i][14:]
    data = list(map(int, datain))
    BDATA = str(data)
    LIST = str.encode(BDATA)
    insertList(LIST, COUNTY, STATE, LONG, LAT)        
    if cnt %100==0:print(cnt, end= " ")
    if i == len(ALLdata):
        conn.commit()
        conn.close()
        



In [ ]:
!ls date

In [ ]:
SORT = []
for line in NEW_LIST:
    SORT.append([line[0][-1],line[2],line[3],line[4],line[5]])
    
    
for line in sorted(SORT, reverse = True):    
    print(line[0],line[1],line[2],line[3],line[4])


# NUMPY Storing Data in a *npy file

In [ ]:
import requests as req
import os
import numpy as np


!rm data/time_series_covid19_deaths_US.npy

URL ="https://raw.githubusercontent.com/CSSEGISandData/COVID-19/master/csse_covid_19_data/csse_covid_19_time_series/time_series_covid19_deaths_US.csv"

resp = req.get(URL)
content = resp.text
DATALINES = content.splitlines()
DATA=[]
for line in DATALINES:
    # If the county has no deaths, don't list it
    if int(line[-1])>0:
        line=line.split(",")
        DATA.append(line)

filename = "data/"+URL[-33:-4]
print(filename)
np.save(filename, DATA)

In [ ]:
import numpy as np
nfilename = "data/time_series_covid19_deaths_US.npy"
newDATA = np.load(nfilename, allow_pickle=True)
length = (len(newDATA))
print(length)
print(newDATA[640][5:10])
data = newDATA[640][14:]
NUMS=list(map(int,data))
print(NUMS)

In [ ]:
import requests as req
import os
import numpy as np


!rm data/time_series_covid19_deaths_US.npy

URL ="https://raw.githubusercontent.com/CSSEGISandData/COVID-19/master/csse_covid_19_data/csse_covid_19_time_series/time_series_covid19_deaths_US.csv"

resp = req.get(URL)
content = resp.text
DATALINES = content.splitlines()
DATA=[]
for line in DATALINES:
    # If the county has no deaths, don't list it
    if int(line[-1])>0:
        LNZ=line.split(",")
        if len(LNZ) ==145:DATA.append(line)

filename = "data/"+URL[-33:-4]
print(filename)
np.save(filename, DATA)

In [ ]:
import numpy as np
nfilename = "data/time_series_covid19_deaths_US.npy"
newDATA = np.load(nfilename,  allow_pickle=True)
length = (len(newDATA))
print(length)
i=375
nums = newDATA[i][14:]
numd = list(map(int, nums))
print (newDATA[i][5],newDATA[i][6],newDATA[i][9],newDATA[i][8],numd)

In [ ]:
import numpy as np
nfilename = "data/time_series_covid19_deaths_US.npy"
newDATA = np.load(nfilename,  allow_pickle=True)
length = (len(newDATA))
print(length)
for i in range(0,length):
    if "Pinellas" in newDATA[i] and "Florida" in newDATA[i]:
        NUMS=list(map(int,newDATA[i][14:]))
        print(newDATA[i][5],newDATA[i][6],float(newDATA[i][9]),float(newDATA[i][8]),NUMS)

In [ ]:
print(ALLdata[375])

In [ ]:
!rm crono.db

In [ ]:
cnt = 0
import time
import sqlite3
import requests as req
DATE = time.strftime("%m-%d-%H_")

# Create an empty list
ALLdata=[]

URL ="https://raw.githubusercontent.com/CSSEGISandData/COVID-19/master/csse_covid_19_data/csse_covid_19_time_series/time_series_covid19_deaths_US.csv"

resp = req.get(URL)
content = resp.text

#clean the content, then break the content into lines 
content=content.replace(",,",",Ex,")
content=content.replace("(","")
content=content.replace(")","")
content=content.replace("\"","")
lines= content.splitlines()
print (len(lines))
# loop the lines one line at a time
# split each line at the delimiter ` , ` 
# then append the empty list 'ALLdata' with the line (which is now a list):  [line]  
cnt=0
for line in lines:
    cnt=cnt+1
    #convert the splitlines to strings
    if cnt>1:
        line= str(line).split(",")
        ALLdata.append(line)

DATE = time.strftime("%m-%d-%Y")

import os
import sqlite3
def create_db(dbname):
    conn = sqlite3.connect(dbname)
    c=conn.cursor()
    c.execute("CREATE TABLE IF NOT EXISTS BINARIES(DATA BLOB,DATE TEXT,DESCRIPTION TEXT)")
    conn.commit()
    conn.close()
    return

dbname = 'crono.db'
conn = sqlite3.connect(dbname)
c = conn.cursor()
def insertList(dbname, LIST, c=c):
    DATE = time.strftime("%m-%d-%Y")
    DESCRIPTION = STATE
    sql = '''INSERT INTO BINARIES
    (DATA, DATE, DESCRIPTION)
    VALUES(?, ?, ?);'''
    c.execute(sql,[sqlite3.Binary(LIST), DATE, DESCRIPTION])
cnt=0
create_db('crono.db')
for i in range(0, len(ALLdata)):
    cnt=cnt+1
    STATE = ALLdata[i][6]
    meta = [ALLdata[i][5],ALLdata[i][6],float(ALLdata[i][8]),float(ALLdata[i][9])]       
    datain = ALLdata[i][14:]
    data = list(map(int, datain))
    BDATA = str(data)
    LIST = str.encode(BDATA)
    dbname = 'crono.db'
    insertList(dbname, LIST)        
    if cnt %100==0:print(cnt, end= " ")
        
conn.commit()
conn.close()

In [ ]:
print(ALLdata[44][5])

In [ ]:
import requests as req
import time
DATE = time.strftime("%m-%d-%H_")

# Create an empty list
ALLdata=[]

URL ="https://raw.githubusercontent.com/CSSEGISandData/COVID-19/master/csse_covid_19_data/csse_covid_19_time_series/time_series_covid19_deaths_US.csv"

resp = req.get(URL)
content = resp.text

#clean the content, then break the content into lines 
content=content.replace(",,",",Ex,")
content=content.replace("(","")
content=content.replace(")","")
content=content.replace("\"","")
lines= content.splitlines()
print (len(lines))
# loop the lines one line at a time
# split each line at the delimiter ` , ` 
# then append the empty list 'ALLdata' with the line (which is now a list):  [line]  
for line in lines:
    #convert the splitlines to strings
    line= str(line).split(",")
    ALLdata.append(line)

In [ ]:
#deletes the header
del ALLdata[0]
for i in range(0,len(ALLdata)):
    cnt = 0
    if "Arizona" in ALLdata[i] and float(ALLdata[i][8])>0!='0.0':
        cnt=cnt+1
        print("ID=",i,ALLdata[i])
print(cnt)        

In [ ]:
Store = []
#del ALLdata[0]
for i in range(0, len(ALLdata)):
    meta = [ALLdata[i][5],ALLdata[i][6],float(ALLdata[i][8]),float(ALLdata[i][9])]       
    datain = ALLdata[i][14:]
    data = list(map(int, datain))
    Store.append([meta,data,])

In [ ]:
print(len(Store))

In [ ]:
import os
import sqlite3

def create_db(dbname):
    new_db = not os.path.exists(dbname)
    conn = sqlite3.connect(dbname)
    if new_db:
        print ('Creating schema')
        sql = '''create table if not exists BINARIES(
        ID INTEGER PRIMARY KEY AUTOINCREMENT,
        DATA BLOB,
        DATE TEXT,
        DESCRIPTION TEXT);'''
        conn.execute(sql) # shortcut for conn.cursor().execute(sql)
    else:
        print ('Schema exists\n')
        conn.commit()
        conn.close()
    return conn

!rm crono.db
create_db('crono.db')

In [ ]:
cnt=0
for line in Store:
    cn=cnt+1
    if cnt<10:print(line)

In [ ]:
DATE = time.strftime("%m-%d-%Y")
print(DATE)

In [ ]:
import time
DATE = time.strftime("%m-%d-%Y")
def insertList(dbname, LIST):
    DATE = time.strftime("%Y-%m%d%H%M%S")
    DESCRIPTION = STATE
    conn = sqlite3.connect(dbname)
    c = conn.cursor()
    sql = '''INSERT INTO BINARIES
    (DATA, DATE, DESCRIPTION)
    VALUES(?, ?, ?);'''
    c.execute(sql,[sqlite3.Binary(LIST), DATE, DESCRIPTION]) 
    conn.commit()

In [ ]:
bdata = Store
BDATA = str(bdata)
LIST = str.encode(BDATA)
dbname = 'crono.db'
insertList(dbname,  LIST)        

In [ ]:
print(OUT)

In [ ]:
print(Store[0][0])
print(Store[1][1])

In [ ]:
bdata = Store
BDATA = str(bdata)
DATA = str.encode(BDATA)
type(DATA) # ensure it is byte representation


In [ ]:
my_decoded_str = DATA.decode()
print(type(my_decoded_str)) # ensure it is string representation
print(my_decoded_str)

In [ ]:
out = bytes(encode(str(ALLdata)))

In [ ]:
!rm crono.db

In [ ]:
import sqlite3
import os.path
from os import listdir, getcwd
from IPython.core.display import Image 

def getImage_list(rel_path):
    abs_path = os.path.join(os.getcwd(),rel_path)
    print 'abs_path =', abs_path
    dir_files = os.listdir(abs_path)
    return dir_files



def insertImage(dbname, imageFile):
    with open(imageFile, 'rb') as input_file:
        conn = sqlite3.connect(dbname)
        c = conn.cursor()
        ablob = input_file.read()
        base=os.path.basename(imageFile)
        afile, ext = os.path.splitext(base)
        sql = '''INSERT INTO images
        (image, TYPE, imagE)
        VALUES(?, ?, ?);'''
        c.execute(sql,[sqlite3.Binary(ablob), ext, afile]) 
        conn.commit()

def loadimagE(dbname, path):
    conn = sqlite3.connect(dbname)
    c = conn.cursor()
    #conn.execute("DELETE FROM images")
    for fn in image_list:
        imageFile = path+"/"+fn
        insertImage(imageFile)

    for r in c.execute("SELECT rowid, imagE FROM images"):
        print r[0],r[1]
   
    conn.commit()
    conn.close()

def image_id(dbname):
    conn = sqlite3.connect(dbname)
    c = conn.cursor()
    rows = c.execute("SELECT rowid, TYPE, imagE FROM images")
    for row in rows:
        print row[0],row[2]+row[1]    
    return
    
def get_image(dbname,image_id):
    conn = sqlite3.connect(dbname)
    c = conn.cursor()
    c.execute("SELECT image, TYPE, imagE FROM images WHERE id = ?;",(image_id,))
    #sql = "SELECT image, TYPE, imagE FROM images WHERE id = 19"
    param = {'id': image_id}
    #c.execute(sql, param)
    ablob, ext, afile = c.fetchone()
    filename = afile + ext
    with open(filename, 'wb') as output_file:
        output_file.write(ablob)
    return filename

In [ ]:
!ls Custom

In [ ]:
from Custom.uscities import *
city = "Frederick"
cnt=0
DATA =DATA.replace('"','')
data = DATA.splitlines()
for line in data:
    line =line.split(",")
    cnt=cnt+1
    if cnt==1:
        print('  '.join(line[0:11]),"\n")
    if city == line[0]:
        print('  '.join(line[0:11]))

In [ ]:
from Custom.uscities import *
city = "Frederick"
state = "Colorado"
cnt=0
DATA =DATA.replace('"','')
data = DATA.splitlines()
for line in data:
    line =line.split(",")
    cnt=cnt+1
    if cnt==1:
        print(line[0:11],"\n")
    if city == line[0] and state == line[3]:
        print('  '.join(line[0:11]))

In [ ]:
from Custom import uscities
help(uscities)

In [ ]:
!rm data/time_series_covid19_deaths_US.csv.npy

In [ ]:
from Custom.uscities import *
def citylocation(city,state,DATA=DATA):
    cnt=0
    DATA =DATA.replace('"','')
    data = DATA.splitlines()
    for line in data:
        line =line.split(",")
        cnt=cnt+1
        if cnt==1:
            print(line[0:11],"\n")
        if city == line[0] and state == line[3]:
            print('  '.join(line[0:11]))
        
def allcities(city,DATA=DATA):
    cnt=0
    DATA =DATA.replace('"','')
    data = DATA.splitlines()
    for line in data:
        line =line.split(",")
        cnt=cnt+1
        if cnt==1:
            print('  '.join(line[0:11]),"\n")
        if city == line[0]:
            print('  '.join(line[0:11]))        
        
city = "Frederick"        
allcities(city,DATA=DATA)        
        
city = "Frederick"
state = "Colorado"        
citylocation(city,state)        

In [ ]:
from random import randint
def pickrandom():
    i = randint(0,len(newDATA))
    data =newDATA[i].replace('"',"").split(",")
    NUMS=list(map(int,data[14:]))
    county = data[5]
    state = data[6]
    longitude = float(data[9])
    latitude = float(data[8])
    text = ["County and State:",county+", "+state,"\nlongitude & latitude:",longitude,latitude,"\ndata:",NUMS]
    return text
for line in pickrandom():
    print (line)

In [ ]:
from Custom.uscities import *

city = "Frederick"        
allcities(city,DATA=DATA)        
        
city = "Frederick"
state = "Colorado"        
citylocation(city,state)        


In [3]:
from Custom.uscities import *
help(allcities)

Help on function allcities in module Custom.uscities:

allcities(city, DATA='"city","city_ascii","state_id","state_name","county_fips","county_name","county_fips_all","county_name_all","lat","lng","population","density","source","military","incorporated","timezone","ranking","zips","id"\n"South Creek","South Creek","WA","Washington","53053","Pierce","53053","Pierce","46.9994","-122.3921","2500","125","polygon","FALSE","TRUE","America/Los_Angeles","3","98580 98387 98338","1840042075"\n"Roslyn","Roslyn","WA","Washington","53037","Kittitas","53037","Kittitas","47.2507","-121.0989","947","84","polygon","FALSE","TRUE","America/Los_Angeles","3","98941 98068 98925","1840019842"\n"Sprague","Sprague","WA","Washington","53043","Lincoln","53043","Lincoln","47.3048","-117.9713","441","163","polygon","FALSE","TRUE","America/Los_Angeles","3","99032","1840021107"\n"Gig Harbor","Gig Harbor","WA","Washington","53053","Pierce","53053","Pierce","47.3352","-122.5968","9507","622","polygon","FALSE","TRUE",

In [2]:
from Custom.uscities import *


city = "Frederick"        
allcities(city,DATA=DATA)        


city = "Frederick"
state = "Colorado"        
citylocation(city,state)        


city  city_ascii  state_id  state_name  county_fips  county_name  county_fips_all  county_name_all  lat  lng  population 

Frederick  Frederick  CO  Colorado  08123  Weld  08123  Weld  40.1095  -104.9670  12687
Frederick  Frederick  MD  Maryland  24021  Frederick  24021  Frederick  39.4336  -77.4157  154972.0
Frederick  Frederick  OK  Oklahoma  40141  Tillman  40141  Tillman  34.3709  -99.0010  3606.0
Frederick  Frederick  KS  Kansas  20159  Rice  20159  Rice  38.5128  -98.2676  17
Frederick  Frederick  SD  South Dakota  46013  Brown  46013  Brown  45.8321  -98.5069  200
['city', 'city_ascii', 'state_id', 'state_name', 'county_fips', 'county_name', 'county_fips_all', 'county_name_all', 'lat', 'lng', 'population'] 

Frederick  Frederick  CO  Colorado  08123  Weld  08123  Weld  40.1095  -104.9670  12687
